In [1]:
import numpy as np
import matplotlib.pylab as plt
from matplotlib import animation
from IPython.display import HTML

In [303]:
def generate_points(n_points, radius):
    angles = np.random.uniform(0, 2 * np.pi, n_points)  # Random angles
    r = np.sqrt(np.random.uniform(0, 1, n_points)) * radius  # Random radius with correct distribution
    x = r * np.cos(angles)
    y = r * np.sin(angles)
    return np.column_stack((x, y))  # Return as Nx2 array


def points_inside_circle(circle_center, radius, points):
    points = np.array(points)
    h, k = circle_center
    x, y = np.hsplit(points, 2)
    
    # Calculate the squared distance from the point to the circle center
    dist_squared = (x - h) ** 2 + (y - k) ** 2
    radius_squared = radius ** 2

    # Check if the point is inside or on the circle
    result = dist_squared <= radius_squared
    return result.flatten()


def move_point(point, angle, distance):
    # Convert angle to radians
    angle_rad = np.radians(angle + 0.0001)

    # Calculate the movement vector components
    dx = distance * np.cos(angle_rad)
    dy = distance * np.sin(angle_rad)

    # Create a movement vector for all points
    displacement_vector = np.array([dx, dy])

    # Displace the points
    displaced_point = point + displacement_vector

    return displaced_point.astype(np.double)


def displace_points(circle_center, radius, angle, dist, points):  
    points_moved = move_point(points, angle + 0.0001, dist)
    points_out = ~points_inside_circle(circle_center, radius, points_moved)
    points_out_ix = np.arange(points.shape[0])[points_out]
    points_moved_copy = deepcopy(points_moved)
    for p_ix in points_out_ix:
        point = points[p_ix]
        point_moved = points_moved[p_ix]
        inters_vector_line = circle_line_intersection(circle_center, radius, point, point_moved)
        inters_0, inters_1 = inters_vector_line
        inters = [inters_0, inters_1]
        dist_ = [distance.euclidean(i, point_moved) for i in inters]
        new_orig = inters[np.argmax(dist_)]
        left_disp_orig = inters[np.argmin(dist_)]
        left_disp_vec = vector_points(left_disp_orig, point_moved)
        point_moved_new = new_orig + left_disp_vec
        points_moved_copy[p_ix] = point_moved_new
    return points_moved, points_moved_copy, points_out


def angle_displace_points(circle_center, angles, radius, dist, points):
    new_points = []
    for p_ix, point in enumerate(points):
        angle = angles[p_ix] + 0.0001
        dist = 1
        point_moved = move_point(point, angle, dist)
        if ~points_inside_circle(circle_center, radius, point_moved)[0]:
            inters_vector_line = circle_line_intersection(circle_center, radius, point, point_moved)
            inters_0, inters_1 = inters_vector_line
            inters = [inters_0, inters_1]
            dist_ = [distance.euclidean(i, point_moved) for i in inters]
            new_orig = inters[np.argmax(dist_)]
            left_disp_orig = inters[np.argmin(dist_)]
            left_disp_vec = vector_points(left_disp_orig, point_moved)
            point_moved_new = new_orig + left_disp_vec
            new_points.append(point_moved_new)
        else:
            new_points.append(point_moved)
    return np.array(new_points)

def circle_line_intersection(circle_center, radius, point1, point2):
    h, k = circle_center
    x1, y1 = point1
    x2, y2 = point2

    # Calculate slope (m) and intercept (b) of the line
    if x2 - x1 == 0:  # vertical line case
        return []  # A vertical line will not intersect unless it's also at the circle's horizontal level

    m = (y2 - y1) / (x2 - x1)
    b = y1 - m * x1

    # Coefficients of the quadratic equation Ax^2 + Bx + C = 0
    A = 1 + m**2
    B = 2 * (m * (b - k) - h)
    C = (h**2 + (b - k)**2 - radius**2)

    # Calculate the discriminant
    D = B**2 - 4 * A * C

    intersection_points = []

    if D >= 0:  # There are intersections
        # Two possible intersection points if D > 0, one if D = 0
        sqrt_D = np.sqrt(D)

        # Compute both x-coordinates
        x_intersect1 = (-B + sqrt_D) / (2 * A)
        y_intersect1 = m * x_intersect1 + b
        intersection_points.append((x_intersect1, y_intersect1))

        if D > 0:  # Only compute the second intersection point if D > 0
            x_intersect2 = (-B - sqrt_D) / (2 * A)
            y_intersect2 = m * x_intersect2 + b
            intersection_points.append((x_intersect2, y_intersect2))

    return np.array(intersection_points).astype(np.double)


def point_inside_circle(circle_center, radius, point):
    h, k = circle_center
    x, y = point
    
    # Calculate the squared distance from the point to the circle center
    dist_squared = (x - h) ** 2 + (y - k) ** 2
    radius_squared = radius ** 2

    # Check if the point is inside or on the circle
    return dist_squared <= radius_squared


def vector_points(point1, point2):
    x1, y1 = point1
    x2, y2 = point2

    # Calculate the vector components
    dx = x2 - x1
    dy = y2 - y1

    return np.array([dx, dy]).astype(np.double)

In [199]:
circle_diameter = 14
radius = circle_diameter/2
n_points = 500
points = generate_points(n_points, radius)

bool_map = np.zeros(points.shape[0]).astype(bool)
bool_map[points.shape[0]//2 :] = True

In [212]:
fig, ax = plt.subplots(1, 1, figsize=(10,10))
circle = plt.Circle(
    (0, 0), radius=circle_diameter/2, edgecolor="black",
    lw=1, facecolor="none"
)

ax.set_xlim(-10, 10)
ax.set_ylim(-10, 10)

ax.add_patch(circle)

scat = ax.scatter(points[:,0], points[:,1], c="black")

positions = []
for i in range(300):
    pm, points, po_map = displace_points([0,0], radius, 180, 0.05, points)
    positions.append(points)

def animate(i):
    scat.set_offsets(positions[i])
    return (scat,)

plt.tight_layout()

ani = animation.FuncAnimation(fig, animate, repeat=True, frames=len(positions) - 1, interval=10)
HTML(ani.to_html5_video())

In [202]:
fig, ax = plt.subplots(1, 1, figsize=(10,10))
circle = plt.Circle(
    (0, 0), radius=circle_diameter/2, edgecolor="black",
    lw=1, facecolor="none"
)

ax.set_xlim(-10, 10)
ax.set_ylim(-10, 10)

ax.add_patch(circle)

scat = ax.scatter(points[:,0], points[:,1], c="black")
positions = []
for i in range(300):
    copy_points = deepcopy(copy_points)
    pm, points_moved_subset_0, po_map = displace_points([0,0], radius, 180, 0.05, copy_points[bool_map])
    copy_points[bool_map] = points_moved_subset_0
    pm, points_moved_subset_1, po_map = displace_points([0,0], radius, 0, 0.05, copy_points[~bool_map])
    copy_points[~bool_map] = points_moved_subset_1
    positions.append(copy_points)

def animate(i):
    scat.set_offsets(positions[i])
    return (scat,)

ani = animation.FuncAnimation(fig, animate, repeat=True, frames=len(positions) - 1, interval=10)
plt.tight_layout()
HTML(ani.to_html5_video())

# FFwriter = animation.FFMpegWriter(fps=60)
# ani.save('animation.mp4', writer = FFwriter)

(500, 2)

In [218]:
bool_maps = []
for i in np.array_split(np.arange(points.shape[0]),3):
    bool_map_3 = np.zeros(points.shape[0]).astype(bool)
    bool_map_3[i] = True
    bool_maps.append(bool_map_3)

In [304]:
fig, ax = plt.subplots(1, 1, figsize=(10,10))
circle = plt.Circle(
    (0, 0), radius=circle_diameter/2, edgecolor="black",
    lw=1, facecolor="none"
)

ax.set_xlim(-10, 10)
ax.set_ylim(-10, 10)

ax.add_patch(circle)

scat = ax.scatter(points[:,0], points[:,1], c="black")
positions = []

rand_ang = np.random.uniform(0, 360, np.sum(bool_maps[2]).astype(int))
ang_90 = np.repeat(90.0, np.sum(bool_map_3))
copy_points = deepcopy(copy_points)
for i in range(300):
    copy_points = deepcopy(copy_points)
    pm, points_moved_subset_0, po_map = displace_points([0,0], radius, 180, 0.05, copy_points[bool_maps[0]])
    pm, points_moved_subset_1, po_map = displace_points([0,0], radius, 0, 0.05, copy_points[bool_maps[1]])
    # pm, points_moved_subset_2, po_map = displace_points([0,0], radius, 90, 0.05, copy_points[bool_maps[2]])
    points_moved_subset_2 = angle_displace_points([0,0], ang_90, radius, 0.05, copy_points[bool_maps[2]])
    copy_points[bool_maps[0]] = points_moved_subset_0
    copy_points[bool_maps[1]] = points_moved_subset_1
    copy_points[bool_maps[2]] = points_moved_subset_2

    positions.append(copy_points)

def animate(i):
    scat.set_offsets(positions[i])
    return (scat,)

ani = animation.FuncAnimation(fig, animate, repeat=True, frames=len(positions) - 1, interval=10)

HTML(ani.to_html5_video())
# plt.close('all')

In [6]:
np.arange(0.05, 1.0, 0.05)[::-1]

array([0.95, 0.9 , 0.85, 0.8 , 0.75, 0.7 , 0.65, 0.6 , 0.55, 0.5 , 0.45,
       0.4 , 0.35, 0.3 , 0.25, 0.2 , 0.15, 0.1 , 0.05])

In [4]:
len(())

0

In [6]:
sum([True, True]) == 2

True

In [10]:
list(np.arange(7))[-2:]

[np.int64(5), np.int64(6)]